In [ ]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
from ydata_profiling import ProfileReport
#pip install rdkit-pypi
from rdkit import Chem
from rdkit.Chem.Draw import IPythonConsole
from rdkit.Chem import Draw

import shap

from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.neighbors import KNeighborsRegressor
import xgboost as xgb
from sklearn.svm import SVR
from sklearn.ensemble import GradientBoostingRegressor



from sklearn.metrics import make_scorer ,mean_squared_error, mean_absolute_error, r2_score, explained_variance_score, max_error

from scipy.stats import skew

from sklearn.preprocessing import StandardScaler , FunctionTransformer

from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_validate , cross_val_score


This train dataset contains both single-junctional OSCs with nonfullerene acceptors and tandem OSCs with nonfullerene acceptors (NFA).
The references of these different data and articles studied will be mentioned at the end of this work. 

We have collected the names of the donors and acceptors whose smiles had been lied to. ( Because one of the constraints of this project is that there was no software at our disposal allowing to find the smiles from the shortened names of molecules ) and with the help of the python library mordered which is an alternative to the software DRAGON 2.0 usually used ( which is not available anymore ) to generate descriptors ( about 1826 ) . This makes a total of about 3652 descriptors managed in our case ( 1826 for D and 1826 for A )



* The data of type D-NFA with single junction were collected and contained the quite a lot of information of which those which we retained were the name of the Donors, Acceptors, the corresponding smiles, PCE of the combinations D-A.

* Concerning the other type of data (D-NFA tandem), there were no smiles in the base. The collected data were only the PCE, the names of the D and A and we used the list of smiles at our disposal and mapped these smiles to the names of each molecule of this data.

**Note :**  You will see in this dataset some data where the names of the acceptors are not mentinonated ( and replaced by the NaN values ) . These data belong in fact to the category of D-NFA with single junction and the data were found as they are, but since it is especially the smiles which were important to generate the descriptors, these data were kept and used within the framework of our work.


How this was done will be detailed in another notebook.


In [ ]:
data=pd.read_csv("data/train_data_with_virtualdesciptors.csv", low_memory=False)


acc_SMILES_column = data.pop('acc_SMILES')
data.insert(0, 'acc_SMILES', acc_SMILES_column)
don_SMILES_column= data.pop('don_SMILES')
data.insert(1, 'don_SMILES', don_SMILES_column)
reported_acc_column = data.pop('Reported Acceptor')
data.insert(2, 'Reported Acceptor', reported_acc_column)
reported_don_column = data.pop('Reported Donor ')
data.insert(3, 'Reported Donor ', reported_don_column)



In [3]:
pd.set_option('display.max_columns', None)
data.head()

acc_SMILES  \
0  CCc1ccc(C2(c3ccc(CC)cc3)c3cc4c(cc3-c3sc5cc(/C=...   
1  CCc1ccc(C2(c3ccc(CC)cc3)c3cc4c(cc3-c3sc5cc(/C=...   
2  CCc1c(/C=C2\C(=O)c3cc(F)c(F)cc3C2=C(C#N)C#N)sc...   
3  CCC1(CC)c2cc3c(cc2-c2sc(/C=C4\C(=O)c5ccccc5C4=...   
4  O=C1C2=C(C=CC=C2)C(/C1=C/C3=CC(C4(C5=CC=C(CCCC...   

                                          don_SMILES Reported Acceptor  \
0  CCCc1sc(-c2c3cc(-c4cc(C(=O)CC)c(-c5ccc(-c6sc(-...             IT-4F   
1  CCN1C(=O)/C(=C\c2csc(-c3ccc(-c4ccc(-c5sc(-c6cc...              ITIC   
2  CCOC(=O)/C(C#N)=C/c1ccc(-c2sc(-c3cc4c(-c5ccc(C...                Y6   
3  CCOC(=O)/C(C#N)=C\c1cc(CC)c(-c2ccc(-c3sc(-c4cc...              IDIC   
4  CCOC(=O)/C(C#N)=C\c1cc(CC)c(-c2ccc(-c3sc(-c4cc...               NaN   

  Reported Donor    ABC_donor  ABCGG_donor  nAcid_donor  nBase_donor  \
0       PBDT-3TCO  124.327252    84.118682            0            0   
1           PTIBT   68.613631    46.808443            0            0   
2          3BDT-5   96.424552    65.129270            0            0   
3           SM-Cl   66.015914    47.400457            0            0   
4           SM-Cl   66.015914    47.400457            0            0   

   SpAbs_A_donor  SpMax_A_donor  SpDiam_A_donor  SpAD_A_donor  SpMAD_A_donor  \
0     204.028157       2.635164        5.121447    204.028157       1.324858   
1     113.422146       2.538887        4.841794    113.422146       1.350264   
2     160.252377       2.651864        5.137436    160.252377       1.335436   
3     109.669402       2.632854        5.119109    109.669402       1.305588   
4     109.669402       2.632854        5.119109    109.669402       1.305588   

   LogEE_A_donor  VE1_A_donor  VE2_A_donor  VE3_A_donor   VR1_A_donor  \
0       6.002737     8.308157     0.053949     4.851605  13929.401861   
1       5.404533     7.516350     0.089480     4.145312   2202.665574   
2       5.750998     7.829957     0.065250     4.542864  33798.624380   
3       5.376136     5.628559     0.067007     3.856085  32903.197765   
4       5.376136     5.628559     0.067007     3.856085  32903.197765   

   VR2_A_donor  VR3_A_donor  nAromAtom_donor  nAromBond_donor  nAtom_donor  \
0    90.450661    12.276125              111              117          242   
1    26.222209     9.825655               63               63          131   
2   281.655203    12.913082               86               92          196   
3   391.704735    12.529557               52               54          138   
4   391.704735    12.529557               52               54          138   

   nHeavyAtom_donor  nSpiro_donor  nBridgehead_donor  nHetero_donor  nH_donor  \
0               154             0                  0             33        88   
1                84             0                  0             15        47   
2               120             0                  0             22        76   
3                84             0                  0             18        54   
4                84             0                  0             18        54   

   nB_donor  nC_donor  nN_donor  nO_donor  nS_donor  nP_donor  nF_donor  \
0         0       121         0         6        21         0         6   
1         0        69         3         3         9         0         0   
2         0        98         2         4        16         0         0   
3         0        66         2         4        10         0         0   
4         0        66         2         4        10         0         0   

   nCl_donor  nBr_donor  nI_donor  nX_donor  ATS0dv_donor  ATS1dv_donor  \
0          0          0         0         6   1937.333333   1919.666667   
1          0          0         0         0    986.000000   1082.666667   
2          0          0         0         0   1317.111111   1409.333333   
3          2          0         0         2    941.654321    973.555556   
4          2          0         0         2    941.654321    973.555556   

   ATS2dv_donor  ATS3dv_donor  ATS4dv_donor  ATS5

# DATA PREPROCESSING

In [4]:
data.shape

(1280, 3657)

In [5]:
data.describe()

ABC_donor  ABCGG_donor  nAcid_donor  nBase_donor  SpAbs_A_donor  \
count  1280.000000  1280.000000       1280.0       1280.0    1280.000000   
mean    115.144566    76.807412          0.0          0.0     189.352412   
std      33.486267    20.495867          0.0          0.0      54.816975   
min      34.422171    27.752886          0.0          0.0      57.516517   
25%      97.791043    67.506120          0.0          0.0     160.643945   
50%     133.085127    87.677503          0.0          0.0     219.375997   
75%     137.741465    91.420307          0.0          0.0     225.138222   
max     206.311039   129.996301          0.0          0.0     342.812273   

       SpMax_A_donor  SpDiam_A_donor  SpAD_A_donor  SpMAD_A_donor  \
count    1280.000000     1280.000000   1280.000000    1280.000000   
mean        2.633332        5.102145    189.352412       1.338924   
std         0.037965        0.103328     54.816975       0.015732   
min         2.518369        4.764818     57.516517       1.285203   
25%         2.632939        5.122446    160.643945       1.334269   
50%         2.647700        5.133272    219.375997       1.340108   
75%         2.648991        5.135246    225.138222       1.354173   
max         2.901166        5.736760    342.812273       1.383039   

       LogEE_A_donor  VE1_A_donor  VE2_A_donor  VE3_A_donor   VR1_A_donor  \
count    1280.000000  1280.000000  1280.000000  1280.000000  1.280000e+03   
mean        5.863100     9.032964     0.069279     4.771083  2.240018e+11   
std         0.403963     1.433163     0.020214     0.565183  8.014133e+12   
min         4.731587     4.283864     0.022312     3.233786  4.594016e+02   
25%         5.764914     8.510837     0.061370     4.626247  4.681626e+03   
50%         6.072076     9.466129     0.062235     5.095773  6.396904e+03   
75%         6.106171    10.082102     0.070924     5.132521  7.464048e+03   
max         6.505196    11.442980     0.131072     5.664220  2.867223e+14   

        VR2_A_donor  VR3_A_donor  nAromAtom_donor  nAromBond_donor  \
count  1.280000e+03  1280.000000      1280.000000      1280.000000   
mean   1.166676e+09    11.177502       106.807031       113.206250   
std    4.174028e+10     1.414886        32.642798        34.601219   
min    1.044095e+01     7.611529        30.000000        30.000000   
25%    3.736275e+01    10.936307        90.000000        99.000000   
50%    3.948706e+01    11.548581       126.000000       132.000000   
75%    5.070309e+01    11.605701       126.000000       132.000000   
max    1.493346e+12    36.244446       210.000000       225.000000   

       nAtom_donor  nHeavyAtom_donor  nSpiro_donor  nBridgehead_donor  \
count  1280.000000       1280.000000        1280.0             1280.0   
mean    221.110156        141.110938           0.0                0.0   
std      62.077882         40.362976           0.0                0.0   
min      86.000000         44.000000           0.0                0.0   
25%     185.000000        120.000000           0.0                0.0   
50%     254.000000        162.000000           0.0                0.0   
75%     254.000000        168.000000           0.0                0.0   
max     422.000000        252.000000           0.0                0.0   

       nHetero_donor     nH_donor  nB_donor     nC_donor     nN_donor  \
count    1280.000000  1280.000000    1280.0  1280.000000  1280.000000   
mean       29.717188    79.999219       0.0   111.393750     2.399219   
std         9.092850    23.830208       0.0    32.439702     3.952315   
min         6.000000    26.000000       0.0    38.000000     0.000000   
25%        27.000000    65.000000       0.0    93.000000     0.000000   
50%        30.000000    86.000000       0.0   132.000000     0.000000   
75%        36.000000    92.000000       0.0   132.000000     6.000000   
max        66.000000   173.000000       0.0   216.000000    18.000000   

          nO_donor     nS_donor  nP_donor     nF_donor    nCl

In [6]:
zero_cols = data.columns[(data == 0).all()]
len(zero_cols)
data.drop(zero_cols, axis=1, inplace=True)

In [7]:
object_cols = data.select_dtypes(include=['object'])

"""print(len(object_cols))
for i in object_cols.columns :
    try  :
        if (sum(data[i].str.contains('missing 3D coordinate'))>20) or (sum(data[i].str.contains('min()'))>20) or (sum(data[i].str.contains('float division by zero'))>20) or (sum(data[i].str.contains('max()'))>20) :
            data.drop([i],axis=1, inplace=True)
    except :
        pass
"""

excluded_cols = ['acc_SMILES', 'don_SMILES', 'Reported Acceptor', 'Reported Donor ']
object_cols = object_cols.drop(columns=excluded_cols)

data.drop(object_cols.columns,axis=1, inplace=True)

In [8]:
data.shape

(1280, 2320)

In [9]:
data.head()

acc_SMILES  \
0  CCc1ccc(C2(c3ccc(CC)cc3)c3cc4c(cc3-c3sc5cc(/C=...   
1  CCc1ccc(C2(c3ccc(CC)cc3)c3cc4c(cc3-c3sc5cc(/C=...   
2  CCc1c(/C=C2\C(=O)c3cc(F)c(F)cc3C2=C(C#N)C#N)sc...   
3  CCC1(CC)c2cc3c(cc2-c2sc(/C=C4\C(=O)c5ccccc5C4=...   
4  O=C1C2=C(C=CC=C2)C(/C1=C/C3=CC(C4(C5=CC=C(CCCC...   

                                          don_SMILES Reported Acceptor  \
0  CCCc1sc(-c2c3cc(-c4cc(C(=O)CC)c(-c5ccc(-c6sc(-...             IT-4F   
1  CCN1C(=O)/C(=C\c2csc(-c3ccc(-c4ccc(-c5sc(-c6cc...              ITIC   
2  CCOC(=O)/C(C#N)=C/c1ccc(-c2sc(-c3cc4c(-c5ccc(C...                Y6   
3  CCOC(=O)/C(C#N)=C\c1cc(CC)c(-c2ccc(-c3sc(-c4cc...              IDIC   
4  CCOC(=O)/C(C#N)=C\c1cc(CC)c(-c2ccc(-c3sc(-c4cc...               NaN   

  Reported Donor    ABC_donor  ABCGG_donor  SpAbs_A_donor  SpMax_A_donor  \
0       PBDT-3TCO  124.327252    84.118682     204.028157       2.635164   
1           PTIBT   68.613631    46.808443     113.422146       2.538887   
2          3BDT-5   96.424552    65.129270     160.252377       2.651864   
3           SM-Cl   66.015914    47.400457     109.669402       2.632854   
4           SM-Cl   66.015914    47.400457     109.669402       2.632854   

   SpDiam_A_donor  SpAD_A_donor  SpMAD_A_donor  LogEE_A_donor  VE1_A_donor  \
0        5.121447    204.028157       1.324858       6.002737     8.308157   
1        4.841794    113.422146       1.350264       5.404533     7.516350   
2        5.137436    160.252377       1.335436       5.750998     7.829957   
3        5.119109    109.669402       1.305588       5.376136     5.628559   
4        5.119109    109.669402       1.305588       5.376136     5.628559   

   VE2_A_donor  VE3_A_donor   VR1_A_donor  VR2_A_donor  VR3_A_donor  \
0     0.053949     4.851605  13929.401861    90.450661    12.276125   
1     0.089480     4.145312   2202.665574    26.222209     9.825655   
2     0.065250     4.542864  33798.624380   281.655203    12.913082   
3     0.067007     3.856085  32903.197765   391.704735    12.529557   
4     0.067007     3.856085  32903.197765   391.704735    12.529557   

   nAromAtom_donor  nAromBond_donor  nAtom_donor  nHeavyAtom_donor  \
0              111              117          242               154   
1               63               63          131                84   
2               86               92          196               120   
3               52               54          138                84   
4               52               54          138                84   

   nHetero_donor  nH_donor  nC_donor  nN_donor  nO_donor  nS_donor  nF_donor  \
0             33        88       121         0         6        21         6   
1             15        47        69         3         3         9         0   
2             22        76        98         2         4        16         0   
3             18        54        66         2         4        10         0   
4             18        54        66         2         4        10         0   

   nCl_donor  nX_donor  ATS0dv_donor  ATS1dv_donor  ATS2dv_donor  \
0          0         6   1937.333333   1919.666667   2830.666667   
1          0         0    986.000000   1082.666667   1586.666667   
2          0         0   1317.111111   1409.333333   2055.333333   
3          2         2    941.654321    973.555556   1367.555556   
4          2         2    941.654321    973.555556   1367.555556   

   ATS3dv_donor  ATS4dv_donor  ATS5dv_donor  ATS6dv_donor  ATS7dv_donor  \
0   2974.555556   3157.000000   3492.666667   3768.555556   3938.333333   
1   1573.888889   1482.333333   1576.666667   1452.111111   1451.000000   
2   2168.000000   2416.666667   2496.333333   2608.222222   2606.333333   
3   1406.370370   1495.333333   1524.777778   1591.925926   1520.481481   
4   1406.370370   1495.333333   1524.777778   1591.925926   1520.481481   

   ATS8dv_donor  ATS0d_donor  ATS1d_donor  ATS2d_donor  ATS3d_donor  \
0   3899.666667        982.0       1261.0       2039.0       2253.0   
1  

* Missing Values

In [10]:
def PrintedNbrNanValues(data):
    a=dict(data.isnull().sum())
    for i,j in a.items() :
        if j>=1 :
            print(i , j)

PrintedNbrNanValues(data)

Reported Acceptor 289
ABC 1
ABCGG 1
nAcid 1
nBase 1
nAromAtom 1
nAromBond 1
nAtom 1
nHeavyAtom 1
nSpiro 1
nBridgehead 1
nHetero 1
nH 1
nB 1
nC 1
nN 1
nO 1
nS 1
nP 1
nF 1
nCl 1
nBr 1
nI 1
nX 1
ATS0dv 1
ATS1dv 1
ATS2dv 1
ATS3dv 1
ATS4dv 1
ATS5dv 1
ATS6dv 1
ATS7dv 1
ATS8dv 1
ATS0d 1
ATS1d 1
ATS2d 1
ATS3d 1
ATS4d 1
ATS5d 1
ATS6d 1
ATS7d 1
ATS8d 1
ATS0Z 1
ATS1Z 1
ATS2Z 1
ATS3Z 1
ATS4Z 1
ATS5Z 1
ATS6Z 1
ATS7Z 1
ATS8Z 1
ATS0m 1
ATS1m 1
ATS2m 1
ATS3m 1
ATS4m 1
ATS5m 1
ATS6m 1
ATS7m 1
ATS8m 1
ATS0v 1
ATS1v 1
ATS2v 1
ATS3v 1
ATS4v 1
ATS5v 1
ATS6v 1
ATS7v 1
ATS8v 1
ATS0se 1
ATS1se 1
ATS2se 1
ATS3se 1
ATS4se 1
ATS5se 1
ATS6se 1
ATS7se 1
ATS8se 1
ATS0pe 1
ATS1pe 1
ATS2pe 1
ATS3pe 1
ATS4pe 1
ATS5pe 1
ATS6pe 1
ATS7pe 1
ATS8pe 1
ATS0are 1
ATS1are 1
ATS2are 1
ATS3are 1
ATS4are 1
ATS5are 1
ATS6are 1
ATS7are 1
ATS8are 1
ATS0p 1
ATS1p 1
ATS2p 1
ATS3p 1
ATS4p 1
ATS5p 1
ATS6p 1
ATS7p 1
ATS8p 1
ATS0i 1
ATS1i 1
ATS2i 1
ATS3i 1
ATS4i 1
ATS5i 1
ATS6i 1
ATS7i 1
ATS8i 1
AATS0dv 1
AATS1dv 1
AATS2dv 1
AATS3dv 1
AAT

In [11]:
data.dropna(subset=['ATSC7v'], inplace=True)
PrintedNbrNanValues(data)

Reported Acceptor 288


In [12]:
"""profile = ProfileReport(
    data,
    title="Profiling Report For D-NFA dataset with descriptors ",
    html={'style':{'full_width':True}}
)

profile.to_file(output_file = "data_NFA_with_descriptors-profile.html")"""

'profile = ProfileReport(\n    data,\n    title="Profiling Report For D-NFA dataset with descriptors ",\n    html={\'style\':{\'full_width\':True}}\n)\n\nprofile.to_file(output_file = "data_NFA_with_descriptors-profile.html")'

In [13]:
corr_matrix = data.corr()


In [14]:
corr_matrix

ABC_donor  ABCGG_donor  SpAbs_A_donor  SpMax_A_donor  \
ABC_donor        1.000000     0.995606       0.999799       0.730261   
ABCGG_donor      0.995606     1.000000       0.995234       0.736810   
SpAbs_A_donor    0.999799     0.995234       1.000000       0.727221   
SpMax_A_donor    0.730261     0.736810       0.727221       1.000000   
SpDiam_A_donor   0.752526     0.746564       0.750581       0.923435   
...                   ...          ...            ...            ...   
WPol             0.181236     0.184774       0.181823       0.159337   
Zagreb1          0.172315     0.176447       0.173164       0.155500   
Zagreb2          0.181588     0.185111       0.182251       0.159202   
mZagreb2         0.146614     0.152504       0.147991       0.144451   
PCE (%)          0.429094     0.429803       0.426117       0.335084   

                SpDiam_A_donor  SpAD_A_donor  SpMAD_A_donor  LogEE_A_donor  \
ABC_donor             0.752526      0.999799       0.672889       0.979180   
ABCGG_donor           0.746564      0.995234       0.640942       0.976154   
SpAbs_A_donor         0.750581      1.000000       0.676290       0.978358   
SpMax_A_donor         0.923435      0.727221       0.672789       0.800928   
SpDiam_A_donor        1.000000      0.750581       0.665597       0.819279   
...                        ...           ...            ...            ...   
WPol                  0.132695      0.181823       0.173131       0.187023   
Zagreb1               0.127448      0.173164       0.170720       0.179654   
Zagreb2               0.133101      0.182251       0.175337       0.188043   
mZagreb2              0.114646      0.147991       0.156019       0.156567   
PCE (%)               0.403379      0.426117       0.236111       0.440152   

                VE1_A_donor  VE2_A_donor  VE3_A_donor  VR1_A_donor  \
ABC_donor          0.916415    -0.910561     0.976147     0.036649   
ABCGG_donor        0.919668    -0.905631     0.975261     0.032315   
SpAbs_A_donor      0.914651    -0.910024     0.975085     0.036065   
SpMax_A_donor      0.665400    -0.828620     0.772510     0.197406   
SpDiam_A_donor     0.653068    -0.869097     0.783759     0.171824   
...                     ...          ...          ...          ...   
WPol               0.200491    -0.156259     0.194916     0.006680   
Zagreb1            0.191737    -0.150022     0.187393     0.004643   
Zagreb2            0.201078    -0.157291     0.195984     0.005537   
mZagreb2           0.165158    -0.132067     0.163342     0.000570   
PCE (%)            0.411889    -0.435995     0.437016     0.040734   

                VR2_A_donor  VR3_A_donor  nAromAtom_donor  nAromBond_donor  \
ABC_donor          0.036649     0.787257         0.986482         0.982944   
ABCGG_donor        0.032315     0.776306         0.972764         0.968859   
SpAbs_A_donor      0.036065     0.787184         0.986658         0.982971   
SpMax_A_donor      0.197406     0.785575         0.708199         0.725816   
SpDiam_A_donor     0.171824     0.813915         0.745438         0.764406   
...                     ...          ...              ...              ...   
WPol               0.006680     0.119543         0.181381         0.182515   
Zagreb1            0.004643     0.113140         0.173075         0.174940   
Zagreb2            0.005537     0.119994         0.182199         0.183407   
mZagreb2           0.000570     0.095949         0.147045         0.150274   
PCE (%)            0.040734     0.386910         0.412423         0.408335   

                nAtom_donor  nHeavyAtom_donor  nHetero_donor  nH_donor  \
ABC_donor          0.976552          0.999531       0.894694  0.850923   
ABCGG_donor        0.977775          0.996328       0.899343  0.859533   
SpAbs_A_donor      0.979270          0.999535       0.890023  0.857998   
SpMax_A_donor      0.675306          0.723545       0.665130  0.533638   
SpDiam_A_donor     0.694527          0.748401       0.734697  0.54

In [29]:
corr_matrix = corr_matrix.abs()

mask = np.triu(np.ones_like(corr_matrix, dtype=bool))

#to_drop = [c for c in corr_matrix.columns if any(corr_matrix[c] > 0.8)]
to_drop = [c for c in corr_matrix.columns if any(corr_matrix[c].loc[corr_matrix.index != c] > 0.8)]

print(len(to_drop))


2035


In [25]:
print(len(to_drop))

2139


In [ ]:
data = data.drop(columns=to_drop)

# Model Construction 

To select the appropriate regression model , we must train and validate differents models on our train/validation data and compare the metrics

* XGBoost
* Random Forest
* Desicion Trees
* K-nearest neighbors

# MODEL TEST (APPLICATION)


664 unique acceptors and 235 unique donors were identified. And so 664*235 combinations were generated, the corresponding smiles were identified and the descriptors were calculated to constitute our test dataset.